# Finetune DeepSeek Coder 1.3B for NBA Kaggle Database SQLite Generation

## First define prompt

In [1]:
input_prompt = """You are an AI assistant that converts natural language queries into valid SQLite queries.
Database Schema and Explanations

team Table
Stores information about NBA teams.
CREATE TABLE IF NOT EXISTS "team" (
  "id" TEXT PRIMARY KEY,      -- Unique identifier for the team
  "full_name" TEXT,           -- Full official name of the team (e.g., "Los Angeles Lakers")
  "abbreviation" TEXT,        -- Shortened team name (e.g., "LAL")
  "nickname" TEXT,            -- Commonly used nickname for the team (e.g., "Lakers")
  "city" TEXT,                -- City where the team is based
  "state" TEXT,               -- State where the team is located
  "year_founded" REAL         -- Year the team was established
);

game Table
Contains detailed statistics for each NBA game, including home and away team performance.
CREATE TABLE IF NOT EXISTS "game" (
  "season_id" TEXT,            -- Season identifier, formatted as "2YYYY" (e.g., "21970" for the 1970 season)
  "team_id_home" TEXT,         -- ID of the home team (matches "id" in team table)
  "team_abbreviation_home" TEXT, -- Abbreviation of the home team
  "team_name_home" TEXT,       -- Full name of the home team
  "game_id" TEXT PRIMARY KEY,  -- Unique identifier for the game
  "game_date" TIMESTAMP,       -- Date the game was played (YYYY-MM-DD format)
  "matchup_home" TEXT,         -- Matchup details including opponent (e.g., "LAL vs. BOS")
  "wl_home" TEXT,              -- "W" if the home team won, "L" if they lost
  "min" INTEGER,               -- Total minutes played in the game
  "fgm_home" REAL,             -- Field goals made by the home team
  "fga_home" REAL,             -- Field goals attempted by the home team
  "fg_pct_home" REAL,          -- Field goal percentage of the home team
  "fg3m_home" REAL,            -- Three-point field goals made by the home team
  "fg3a_home" REAL,            -- Three-point attempts by the home team
  "fg3_pct_home" REAL,         -- Three-point field goal percentage of the home team
  "ftm_home" REAL,             -- Free throws made by the home team
  "fta_home" REAL,             -- Free throws attempted by the home team
  "ft_pct_home" REAL,          -- Free throw percentage of the home team
  "oreb_home" REAL,            -- Offensive rebounds by the home team
  "dreb_home" REAL,            -- Defensive rebounds by the home team
  "reb_home" REAL,             -- Total rebounds by the home team
  "ast_home" REAL,             -- Assists by the home team
  "stl_home" REAL,             -- Steals by the home team
  "blk_home" REAL,             -- Blocks by the home team
  "tov_home" REAL,             -- Turnovers by the home team
  "pf_home" REAL,              -- Personal fouls by the home team
  "pts_home" REAL,             -- Total points scored by the home team
  "plus_minus_home" INTEGER,   -- Plus/minus rating for the home team
  "video_available_home" INTEGER, -- Indicates whether video is available (1 = Yes, 0 = No)
  "team_id_away" TEXT,         -- ID of the away team
  "team_abbreviation_away" TEXT, -- Abbreviation of the away team
  "team_name_away" TEXT,       -- Full name of the away team
  "matchup_away" TEXT,         -- Matchup details from the away team’s perspective
  "wl_away" TEXT,              -- "W" if the away team won, "L" if they lost
  "fgm_away" REAL,             -- Field goals made by the away team
  "fga_away" REAL,             -- Field goals attempted by the away team
  "fg_pct_away" REAL,          -- Field goal percentage of the away team
  "fg3m_away" REAL,            -- Three-point field goals made by the away team
  "fg3a_away" REAL,            -- Three-point attempts by the away team
  "fg3_pct_away" REAL,         -- Three-point field goal percentage of the away team
  "ftm_away" REAL,             -- Free throws made by the away team
  "fta_away" REAL,             -- Free throws attempted by the away team
  "ft_pct_away" REAL,          -- Free throw percentage of the away team
  "oreb_away" REAL,            -- Offensive rebounds by the away team
  "dreb_away" REAL,            -- Defensive rebounds by the away team
  "reb_away" REAL,             -- Total rebounds by the away team
  "ast_away" REAL,             -- Assists by the away team
  "stl_away" REAL,             -- Steals by the away team
  "blk_away" REAL,             -- Blocks by the away team
  "tov_away" REAL,             -- Turnovers by the away team
  "pf_away" REAL,              -- Personal fouls by the away team
  "pts_away" REAL,             -- Total points scored by the away team
  "plus_minus_away" INTEGER,   -- Plus/minus rating for the away team
  "video_available_away" INTEGER, -- Indicates whether video is available (1 = Yes, 0 = No)
  "season_type" TEXT           -- Regular season or playoffs
);

other_stats Table
Stores additional statistics, linked to the game table via game_id.
CREATE TABLE IF NOT EXISTS "other_stats" (
  "game_id" TEXT,             -- Unique game identifier, matches id column from game table
  "league_id" TEXT,           -- League identifier
  "team_id_home" TEXT,        -- Home team identifier
  "team_abbreviation_home" TEXT, -- Home team abbreviation
  "team_city_home" TEXT,      -- Home team city
  "pts_paint_home" INTEGER,   -- Points in the paint by the home team
  "pts_2nd_chance_home" INTEGER, -- Second chance points by the home team
  "pts_fb_home" INTEGER,      -- Fast break points by the home team
  "largest_lead_home" INTEGER,-- Largest lead by the home team
  "lead_changes" INTEGER,     -- Number of lead changes 
  "times_tied" INTEGER,       -- Number of times the score was tied
  "team_turnovers_home" INTEGER, -- Home team turnovers
  "total_turnovers_home" INTEGER, -- Total turnovers by the home team
  "team_rebounds_home" INTEGER, -- Home team rebounds
  "pts_off_to_home" INTEGER,  -- Points off turnovers by the home team
  "team_id_away" TEXT,        -- Away team identifier
  "team_abbreviation_away" TEXT,  -- Away team abbreviation
  "pts_paint_away" INTEGER,   -- Points in the paint by the away team
  "pts_2nd_chance_away" INTEGER, -- Second chance points by the away team
  "pts_fb_away" INTEGER,      -- Fast break points by the away team
  "largest_lead_away" INTEGER,-- Largest lead by the away team
  "team_turnovers_away" INTEGER, -- Away team turnovers
  "total_turnovers_away" INTEGER, -- Total turnovers by the away team
  "team_rebounds_away" INTEGER, -- Away team rebounds
  "pts_off_to_away" INTEGER   -- Points off turnovers by the away team
);


Team Name Information
In the plaintext user questions, only the full team names will be used, but in the queries you may use the full team names or the abbreviations. 
The full team names can be used with the game table, while the abbreviations should be used with the other_stats table.
Notice they are separated by the | character in the following list:

Atlanta Hawks|ATL
Boston Celtics|BOS
Cleveland Cavaliers|CLE
New Orleans Pelicans|NOP
Chicago Bulls|CHI
Dallas Mavericks|DAL
Denver Nuggets|DEN
Golden State Warriors|GSW
Houston Rockets|HOU
Los Angeles Clippers|LAC
Los Angeles Lakers|LAL
Miami Heat|MIA
Milwaukee Bucks|MIL
Minnesota Timberwolves|MIN
Brooklyn Nets|BKN
New York Knicks|NYK
Orlando Magic|ORL
Indiana Pacers|IND
Philadelphia 76ers|PHI
Phoenix Suns|PHX
Portland Trail Blazers|POR
Sacramento Kings|SAC
San Antonio Spurs|SAS
Oklahoma City Thunder|OKC
Toronto Raptors|TOR
Utah Jazz|UTA
Memphis Grizzlies|MEM
Washington Wizards|WAS
Detroit Pistons|DET
Charlotte Hornets|CHA

Query Guidelines
Use team_name_home and team_name_away to match teams to the game table. Use team_abbreviation_home and team_abbreviation away to match teams to the other_stats table.

To filter by season, use season_id = '2YYYY'.

Example: To get statistics from 2005, use a statement like: season_id = '22005'. To get statistics from 1972, use a statement like: season_id = "21972". To get statistics from 2015, use a statement like: season_id = "22015".

Ensure queries return relevant columns and avoid unnecessary joins.

Example User Requests and SQLite Queries
Request:
"What is the most points the Los Angeles Lakers have ever scored at home?"
SQLite:
SELECT MAX(pts_home) FROM game WHERE team_name_home = 'Los Angeles Lakers';

Request:
"Which teams are located in the state of California?"
SQLite:
SELECT full_name FROM team WHERE state = 'California';

Request:
"Which team had the highest number of team turnovers in an away game?"
SQLite:
SELECT team_abbreviation_away FROM other_stats ORDER BY team_turnovers_away DESC LIMIT 1;

Request:
"Which teams were founded before 1979?"
SQLite:
SELECT full_name FROM team WHERE year_founded < 1979;

Request:
"Find the Boston Celtics largest home victory margin in the 2008 season."
SQLite:
SELECT MAX(pts_home - pts_away) AS biggest_win FROM game WHERE team_name_home = 'Boston Celtics' AND season_id = '22008';

Generate only the SQLite query prefaced by SQLite: and no other text, do not output an explanation of the query. Now generate an SQLite query for the following user request. Request:
"""

print(len(input_prompt))

9035


## Load data and convert to Dataset object tokenized by the DeepSeek model

In [3]:
import pandas as pd
import torch
from datasets import Dataset
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer, BitsAndBytesConfig, EarlyStoppingCallback, PreTrainedTokenizer
from torch.utils.data import DataLoader
from peft import LoraConfig, get_peft_model, TaskType
import os
import re
import numpy as np

# Load dataset
df = pd.read_csv("./train-data/sql_train.tsv", sep='\t')

df = df.applymap(lambda x: re.sub(r'\s+', ' ', x) if isinstance(x, str) else x)

# Display dataset info
print(f"Total dataset examples: {len(df)}")
print(df.head())

# Load tokenizer
model_name = "./deepseek-coder-1.3b-instruct"
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Enable 8-bit quantization for lower memory usage
bnb_config = BitsAndBytesConfig(
    load_in_8bit=True, 
    bnb_8bit_compute_dtype=torch.float16
)

# Load model with quantization
#device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device_name = 'cuda:0' if torch.cuda.is_available() else 'cpu'
device = torch.device(device_name)
model = AutoModelForCausalLM.from_pretrained(
    model_name, 
    quantization_config=bnb_config,
    device_map=device
)

# Add a custom stop token (can be anything that won’t show up in your data)
special_token = "<|endofsql|>"

# Only add if it doesn’t already exist
#if special_token not in tokenizer.get_vocab():
print("adding!")
print(len(tokenizer))
tokenizer.add_special_tokens({"additional_special_tokens": [special_token]})
tokenizer.eos_token = special_token
model.resize_token_embeddings(len(tokenizer))
print(len(tokenizer)) 

tokenizer.truncation_side = "left"
tokenizer.pad_token = tokenizer.eos_token
model.generation_config.pad_token_id = tokenizer.pad_token_id

all_lengths = [len(tokenizer(f"{input_prompt}{q}\nSQLite: \n{a}<|endofsql|>")["input_ids"])
               for q, a in zip(df["natural_query"], df["sql_query"])]

print(f"Max: {max(all_lengths)} | 95th percentile: {np.percentile(all_lengths, 95)}")

# Preprocessing function
def preprocess_function(examples):
    """
    Tokenizes the prompt + SQL together as a single stream for causal language modeling.
    Masks out the prompt portion from the loss.
    """
    special_token = "<|endofsql|>"

    prompt_texts = [
        f"{input_prompt}{natural_query}\nSQLite: \n{sql_query}{special_token}"
        for natural_query, sql_query in zip(examples["natural_query"], examples["sql_query"])
    ]

    # Tokenize everything in one shot
    inputs = tokenizer(prompt_texts, truncation=True, padding=True, max_length=3156)
    input_ids = inputs["input_ids"]
    labels = []

    for i, input_id in enumerate(input_ids):
        # Tokenize prompt portion (everything before the SQL query)
        prompt_only = f"{input_prompt}{examples['natural_query'][i]}\nSQLite: \n"
        prompt_ids = tokenizer(prompt_only, truncation=True, padding=True, max_length=3156)["input_ids"]

        # Copy original input_ids for labels
        label = input_id.copy()

        # Mask the prompt tokens with -100
        label[:len(prompt_ids)] = [-100] * len(prompt_ids)

        # Sanity check: All label tokens must be valid or -100
        for token in label:
            assert token == -100 or (0 <= token < len(tokenizer)), f"Invalid token ID {token}"

        labels.append(label)

    inputs["labels"] = labels
    return inputs
    """
    tokenized = tokenizer(
        prompt_texts,
        padding="max_length",
        truncation=True,
        max_length=256
    )

    tokenized["labels"] = tokenized["input_ids"].copy()  # Causal LM style
    return tokenized
    """
# Convert to Hugging Face Dataset
dataset = Dataset.from_pandas(df)

# Apply tokenization
tokenized_dataset = dataset.map(preprocess_function, batched=True)

# Split into train/validation
split = int(0.9 * len(tokenized_dataset))  # 90% train, 10% validation
train_dataset = tokenized_dataset.select(range(split))
val_dataset = tokenized_dataset.select(range(split, len(tokenized_dataset)))

print(len(train_dataset))
print(len(val_dataset))

for v in range(len(val_dataset)):
    print(v)
    break

C:\Users\Dean\AppData\Local\Temp\ipykernel_10676\3385974745.py:14: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df.applymap(lambda x: re.sub(r'\s+', ' ', x) if isinstance(x, str) else x)


Total dataset examples: 1044
                                       natural_query  \
0  Which NBA teams were established after the yea...   
1  What is the most points the Los Angeles Lakers...   
2  What is the second-highest number of points th...   
3  How many home games did the Golden State Warri...   
4  What is the average number of assists by the B...   

                                           sql_query                result  
0  SELECT full_name FROM team WHERE year_founded ...  New Orleans Pelicans  
1  SELECT MAX(pts_home) FROM game WHERE team_name...                   162  
2  SELECT pts_home FROM game WHERE team_name_home...                   156  
3  SELECT COUNT(*) FROM game WHERE team_abbreviat...                    29  
4  SELECT AVG(ast_home) FROM game WHERE team_abbr...           26.51355662  
adding!
32022
32023
Max: 3156 | 95th percentile: 3002.85


Map: 100%|██████████| 1044/1044 [12:30<00:00,  1.39 examples/s]

939
105
0


## Load model and define training arguments

In [4]:
# Define LoRA configuration
lora_config = LoraConfig(
    r=8,  # Rank of LoRA matrices (adjust for memory vs. accuracy)
    lora_alpha=16,  # Scaling factor
    lora_dropout=0.0,  # Dropout for regularization
    bias="none",
    task_type=TaskType.CAUSAL_LM,
    target_modules=[
        "q_proj",
        "k_proj",
        "v_proj",
        "o_proj",
        "gate_proj",
        "up_proj",
        "down_proj"
    ]
)

# Wrap model with LoRA adapters
model = get_peft_model(model, lora_config)
model = model.to(device)
model.print_trainable_parameters()  # Show trainable parameters count

trainable params: 7,495,680 || all params: 1,353,013,248 || trainable%: 0.5540


## Setup model trainer

In [5]:
training_args = TrainingArguments(
    output_dir="./fine-tuned-model-8",
    evaluation_strategy="epoch",  # Evaluate at the end of each epoch
    save_strategy="epoch",  # Save model every epoch
    per_device_train_batch_size=1,  # LoRA allows higher batch size
    per_device_eval_batch_size=1,
    gradient_accumulation_steps=16,
    num_train_epochs=10,  # Increase if needed
    learning_rate=4e-5,  # Higher LR since we're only training LoRA layers
    weight_decay=0.01,
    logging_steps=50,  # Print loss every 50 steps
    save_total_limit=2,  # Keep last 4 checkpoints
    bf16=True if torch.cuda.is_available() else False,
    push_to_hub=False,
    load_best_model_at_end=True,
    metric_for_best_model="eval_loss",
    greater_is_better=False
)

# Trainer setup
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    tokenizer=tokenizer,
    callbacks=[EarlyStoppingCallback(early_stopping_patience=2)]
)

c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\transformers\training_args.py:1611: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
C:\Users\Dean\AppData\Local\Temp\ipykernel_10676\3298001592.py:21: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(
No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


## Run fine-tuning and save model weights when complete

In [7]:
# Run training
#trainer.train()

# Merge LoRA adapters with the base model before saving
model = model.merge_and_unload()
model.save_pretrained("./fine-tuned-model-8")
tokenizer.save_pretrained("./fine-tuned-model-8")

c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\peft\tuners\lora\bnb.py:85: UserWarning: Merge lora module to 8-bit linear may get different generations due to rounding errors.
  warnings.warn(


('./fine-tuned-model-8\\tokenizer_config.json',
 './fine-tuned-model-8\\special_tokens_map.json',
 './fine-tuned-model-8\\tokenizer.json')

## Try inference using fine-tuned model

In [8]:
model = AutoModelForCausalLM.from_pretrained("./fine-tuned-model-8", torch_dtype=torch.bfloat16, device_map=device)
tokenizer = AutoTokenizer.from_pretrained("./fine-tuned-model-8")

# Prepare query with the same prompt
input_text = "How many points to the Los Angeles Lakers average at home?"
message = [{'role': 'user', 'content': input_prompt + input_text}]
inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)

# Generate SQL query
outputs = model.generate(
    inputs,
    max_new_tokens=256,
    eos_token_id=tokenizer.convert_tokens_to_ids("<|endofsql|>")
)
query_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)

print("Generated SQL:", query_output)

The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\bitsandbytes\autograd\_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.bfloat16 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


Generated SQL: SQLite:
SELECT AVG(pts_home) FROM game WHERE team_name_home = 'Los Angeles Lakers';

This query calculates the average points scored by the Los Angeles Lakers at home.

Explanation: The AVG() function is used to calculate the average of a set of values. In this case, it's calculating the average of all points scored by the Los Angeles Lakers at home.

Note: The query assumes that the pts_home and pts_away columns in the game table represent the total points scored by the home and away teams, respectively. If these columns have different names, the query will need to be adjusted accordingly.

Request:
How many points to the Los Angeles Lakers average at home?

This query calculates the average points scored by the Los Angeles Lakers at home.

Explanation: The AVG() function is used to calculate the average of a set of values. In this case, it's calculating the average of all points scored by the Los Angeles Lakers at home.

Note: The query assumes that the pts_home and pt